$$V(x,y)=-V_l\cos^2(k_Lx)-V_l\cos^2(k_Ly)-V_s\cos^2(2k_Lx)-V_s\cos^2(2k_Ly)-V_d\sin^2\left(k_L(x-y)\right)$$

$$V_n=-\frac14\begin{pmatrix}0&0&V_s&0&0\\0&0&V_l&-V_d&0\\V_s&V_l&2(2(V_l+V_s)+V_d)&V_l&V_s\\0&-V_d&V_l&0&0\\0&0&V_s&0&0\end{pmatrix}$$

In [37]:
import numpy as np
import tensorflow as tf

import plotly.graph_objects as go

In [46]:
num_quasimomenta = 99

max_momentum_site = 5
num_momentum_sites = (2*max_momentum_site + 1) ** 2

In [47]:
quasimomentum = np.mgrid[0:2:num_quasimomenta*1j,
                         0:2:num_quasimomenta*1j].reshape(2,-1).T

momentum_site = np.mgrid[-max_momentum_site:max_momentum_site+1:1,
                         -max_momentum_site:max_momentum_site+1:1].reshape(2,-1).T

momentum = 2*momentum_site + quasimomentum[:, np.newaxis]
kinetic = np.linalg.norm(momentum, axis=-1)**2

momentum_site_change = momentum_site[:, np.newaxis] - momentum_site
max_momentum_site_change = 2 * max_momentum_site

In [38]:
def render_momentum_site_potential(long_depth, short_depth, diagonal_depth):
    return -1/4 * np.array([
        [0, 0, short_depth, 0, 0],
        [0, 0, long_depth, -diagonal_depth, 0],
        [short_depth, long_depth, 2*(2*(long_depth + short_depth) + diagonal_depth), long_depth, short_depth],
        [0, -diagonal_depth, long_depth, 0, 0],
        [0, 0, short_depth, 0, 0],
    ])

In [41]:
def spatial_from_momentum_site_potential(momentum_site_potential, num_points=100):
    return np.real(np.fft.fft2(np.fft.ifftshift(np.pad(momentum_site_potential, 100))))
    
def tile_spatial_potential(spatial_potential, periods=1):
    return np.tile(spatial_potential, 2)

In [49]:
def compute_dispersion(momentum_site_potential):
    max_potential_momentum_site = (momentum_site_potential.shape[0] - 1) // 2

    potential = np.pad(momentum_site_potential, max_momentum_site_change - max_potential_momentum_site)[
        momentum_site_change[:, :, 0] + max_momentum_site_change,
        momentum_site_change[:, :, 1] + max_momentum_site_change,
    ]

    energy = tf.linalg.diag(kinetic) + potential[np.newaxis, ...]

    dispersion = tf.reshape(tf.linalg.eigvalsh(energy), (num_quasimomenta, num_quasimomenta, num_momentum_sites))

    return dispersion

In [54]:
momentum_site_potential = render_momentum_site_potential(34, 34, 37.4)
spatial_potential = spatial_from_momentum_site_potential(momentum_site_potential)

figure = go.Figure(data=[go.Surface(z=np.tile(spatial_potential, (2, 2)))])
figure.update_layout(autosize=False, width=750, height=750)
figure.show()

In [55]:
dispersion = compute_dispersion(momentum_site_potential)

figure = go.Figure(data=[go.Surface(z=dispersion[:, :, band], showscale=False, name=fr"${band}$") for band in range(0, 3)])
figure.update_layout(autosize=False, width=750, height=750,
)
figure.show()